# Decorators

Function decorators in Python are a powerful and expressive feature for modifying the behavior of functions or methods. They allow you to "decorate" a function without changing its structure, enhancing its functionality or altering its behavior.

At the core, a decorator is a function that takes another function as an argument and extends its behavior without explicitly modifying it. This is achieved by wrapping the original function inside a new function.

## A Simple Example
In the following example, we have a simple decorator that prints a message before and after the "decorated" function is called.

First, we show explicitly wrapping a function by passing a function to the decorator.

In [ ]:
def my_decorator(func):
    def wrapper():
        print("Before the function is called.")
        func()
        print("After the function is called.")
    return wrapper

def say_hello():
    print("Hello!")

say_hello = my_decorator(say_hello)
say_hello()


Note: The names used for the `func` parameter and the inner function (e.g., `wrapper`) are not fixed - you can choose different names, you just need to follow the pattern.

More typically, we will use the `@` symbol to decorate a function:

In [ ]:
@my_decorator
def hello_world():
    print("Hello World!")

hello_world()

In this case, the functionality of `my_decorator` will always be performed whenever the function `hello_world()` is called

## Decorating Functions With Arguments
To decorate functions that accept arguments, modify the wrapper function to accept arguments.  As we do not necessarily know the number of arguments, we'll use `*args` and `**kwargs` to pack/unpack  *positional* and *named* parameters.


In [ ]:
def my_decorator(func):
    def wrapper(*args, **kwargs):
        print("Before the function is called.")
        result = func(*args, **kwargs)
        print("After the function is called.")
        return result
    return wrapper

@my_decorator
def greet(name):
    """Prints hello to someone"""
    print("Hello {}!".format(name))

greet("Alice")

## Introspection on Decorated Functions
As everything (including functions) are objects in Python, we can use instrospection to examine the properties of objecs at runtime.  So we can use the "dunder" properties to get a function's name and documentation string(docstring).

However, when we wrap/decorate a function, by default, we return back the wrapping function's name and docstring:

In [ ]:
print("Name:", greet.__name__, "\nDoc String:",greet.__doc__)

To fix this issue, we need to use the @functools.wraps decorator to preserve the orginal function's attributes.

In [ ]:
import functools

def my_decorator(func):
    @functools.wraps(func)
    def wrapper(*args, **kwargs):
        print("Before the function is called.")
        result = func(*args, **kwargs)
        print("After the function is called.")
        return result
    return wrapper

@my_decorator
def greet(name):
    """Prints hello to someone"""
    print("Hello {}!".format(name))

greet("Bob")
print("\nName:", greet.__name__, "\nDoc String:",greet.__doc__)

## Example Usages

### Logging
We can use decorators to log function calls:

In [ ]:
import functools

def log_function_call(func):
    @functools.wraps(func)
    def wrapper(*args, **kwargs):
        print("Function:", func.__name__)    # remember, functions are objects
        print("Positional arguments:", args)
        print("Keyword arguments:", kwargs)
        result = func(*args, **kwargs)
        print("Result:",result);
        return result
    return wrapper

@log_function_call
def add(x, y):
    """Adds two numbers"""
    return x + y

print(add(1800, 42))
print(add.__doc__)    # Another demostration of using @functools.wrap

## Performance Testing 

Decorators can also be used to measure the execution time of a function:

In [ ]:
import functools
import time

def timing_decorator(func):
    @functools.wraps(func)
    def wrapper(*args, **kwargs):
        start_time = time.time()
        result = func(*args, **kwargs)
        end_time = time.time()
        print("Executing {} took {} seconds".format(func.__name__, end_time - start_time))
        return result
    return wrapper

@timing_decorator
def slow_function():
    time.sleep(2)

slow_function()

## Decorators with Arguments
When you want a decorator to accept arguments, you need to add another function layer:
- **Outer function**: This function takes the decorator arguments.
- **Middle function**: This function takes the function to be decorated.
- **Inner function (wrapper)**: This function wraps original function that adds the extra functionality.

So the general structure appears as -
```python
def decorator_with_arguments(arg1, arg2, ...):
    def middle_function(func):
        @functools.wraps(func)            # Used to maintain decoratored function's "meta" information (e.g., docstring)
        def wrapper(*args, **kwargs):
            # Code to execute before calling the original function
            print("Decorator arguments: {}, {}, ...".format(arg1, arg2, ...))
            result = func(*args, **kwargs)
            # Code to execute after calling the original function
            return result
        return wrapper
    return middle_function
```

**Building upon the performance testing use case:**

One of the difficulties with measuring code performance is that a function executes too fast to measure a function's execution time. To work around
this limitation, execute the function many times to gain an accurate sample. In our exaample, we can modify the timing decorator to take an 
optional parameter for the number of executions.

In [14]:
import functools,  time

def timing_decorator(execution_count = 1):
    def middle_function(func):
        @functools.wraps(func)
        def wrapper(*args, **kwargs):
            start_time = time.time()
            for _ in range(execution_count):
                result = func(*args, **kwargs)
            end_time = time.time()
            print("Executing {} {} times() took {} seconds".format(func.__name__, execution_count, end_time - start_time))
            return result
        return wrapper
    return middle_function


In [15]:
@timing_decorator(3)
def slow_function(seconds):
    """ function sleeps for a certain number of seconds"""
    time.sleep(seconds)

slow_function(1)

Executing slow_function 3 times() took 3.008880853652954 seconds


## Closures and Decorators
A [closure](https://en.wikipedia.org/wiki/Closure_(computer_programming)) is a function object that
retains bindings to the variables that were in its lexical scope 
when the function was created, even after those variables would normally go out of scope. In other words, 
a closure allows a function to access variables from an enclosing scope, even after that scope has finished executing.

Closures are created by defining a function inside another function and then returning the inner function. 
The inner function has access to the variables of the outer function.

Here's a simple example to illustrate closures:

In [17]:
def outer_function(message):
    def inner_function():
        print(message)
    return inner_function

closure = outer_function("Hello, World!")
closure()  # This will print "Hello, World!"

Hello, World!


- `outer_function` takes a parameter `message` and defines an inner function `inner_function` that prints `message`.
- `outer_function` returns `inner_function`, which is a closure because it "remembers" the value of `message` even after `outer_function` has finished executing.

### How Closures Are Used to Implement Decorators

Decorators rely on closures to modify the behavior of functions or methods. Here’s a step-by-step explanation:

1. **Outer Function**: The outer function is called when the decorator is applied. It can take arguments if needed.
2. **Inner Function (Wrapper)**: The inner function, or wrapper, is defined inside the outer function and has access to the outer function’s variables.
3. **Returning the Wrapper**: The outer function returns the inner function, which becomes the decorated function.

### Example of a Basic Decorator Using Closures

Let’s create a simple decorator that adds logging around a function call:

In [19]:
def simple_logger(func):
    def wrapper(*args, **kwargs):
        print("Calling function {} with arguments {} and keyword arguments {}".format(func.__name__,args,kwargs))
        result = func(*args, **kwargs)
        print("Function {} returned {}".format(func.__name__,result))
        return result
    return wrapper

@simple_logger
def add(a, b):
    return a + b

add(2, 3)

Calling function add with arguments (2, 3) and keyword arguments {}
Function add returned 5


5

In this example:
- `simple_logger` is the outer function that takes the original function `func` as an argument.
- `wrapper` is the inner function (closure) that logs the function call and its result.
- `simple_logger` returns `wrapper`, so when `add` is called, the `wrapper` function is actually executed.

### Example of a Decorator with Arguments Using Closures

Let’s create a decorator that logs messages with a custom prefix:

In [23]:
def logger(prefix):
    def decorator(func):
        def wrapper(*args, **kwargs):
            print("{} Calling function {}".format(prefix,func.__name__))
            result = func(*args, **kwargs)
            print("{} Function {} returned {}".format(prefix,func.__name__,result))
            return result
        return wrapper
    return decorator

@logger("DEBUG:")
def multiply(a, b):
    return a * b

multiply(3, 4)


DEBUG: Calling function multiply
DEBUG: Function multiply returned 12


12

- `logger` is the outer function that takes a prefix string as an argument and returns the actual decorator `decorator`.
- `decorator` is a function that takes the original function `func` and returns the `wrapper` function.
- `wrapper` is the closure that has access to both the original function `func` and the `prefix` from `logger`.
- `logger("DEBUG:")` returns `decorator`, which is then applied to `multiply`.

### Why Closures Are Useful for Decorators
Closures allow the decorator to retain state (such as arguments) and modify the behavior of functions or methods in a flexible way. 
By leveraging closures, decorators can:
- Access and manipulate variables from the enclosing scope.
- Maintain state across multiple calls.
- Provide a clean and readable way to extend or alter the behavior of functions and methods.

## Decorators and Flask
While we'll cover Flask in more detail in Section 5, we do want to highlight a couple of uses of decorators within Flask and web-development in general.

### Register Route Handlers
One of the tasks that needs to occur within web applications is to map URLs to the functions that process a specific function.  To do that, we use a the "@route" decorator that takes a URL pattern as an argument.  The HTTP Method may also be specified in the route as well.

```python
from flask import render_template

@app.route('/hello/<name>')
def hello(name=None):
    return render_template('hello.html', name=name)
```

### Require User Authentication

```python
def login_required(view):
    @functools.wraps(view)
    def wrapped_view(**kwargs):
        if g.user is None:
            return redirect(url_for('auth.login'))

        return view(**kwargs)

    return wrapped_view

# source: https://flask.palletsprojects.com/en/3.0.x/tutorial/views/
```

By applying the `@login_required` decorator, we check if a user ID has been established in the current request (another function performs this if the user ID is in the current session).  If the user object is not set, the application redirects the user to the login page. Otherwise, the normal route function(view) is called and returned.


## Aspect-Oriented Programming and Decorators

[Aspect-Oriented Programming (AOP)](https://en.wikipedia.org/wiki/Aspect-oriented_programming) and Python decorators share a common principle: both techniques aim to separate cross-cutting concerns from the main business logic of a program. While AOP is more commonly associated with languages like Java, Python decorators offer a way to implement aspects of AOP in Python. 

AOP aims to increase modularity by allowing the separation of cross-cutting concerns (like logging, security, or error handling) by adding additional behavior to existing code ("an advice") without modifying the code itself.

A decorator is a syntactic feature that adds functionality to an existing function or method (known as advice in AOP terminology). They can be used to implement AOP-like features in Python, handling cross-cutting concerns by "decorating" functions or methods.

### How They Work Together
*Implementing Advice*: In AOP, advice is additional code you want to run at certain points in your program. In Python, decorators can wrap a function or method to execute code before or after the wrapped function, similar to "before" and "after" advice in AOP.

*Pointcut and Join Points*: In AOP, a pointcut defines where an advice should be applied, and a join point is a specific point, like method execution. While Python doesn't have a native concept of pointcuts, decorators can be selectively applied to functions or methods, acting like a manual pointcut.

*Separation of Concerns*: Both AOP and decorators help to separate concerns, such as logging, error handling, or performance measurement from the main business logic. This makes the code cleaner and more maintainable.

*Dynamic Behavior*: Just like AOP, decorators can dynamically add behavior to functions or methods without altering their actual code, which is especially useful in scenarios like authorization, where certain actions need to be performed based on dynamic context.

### Example: click
While not strictly an AOP framework, the [click](https://click.palletsprojects.com/) library, which is used to create command line interfaces,
demonstrates these principles.  Primarily,  `click` helps *separate the concern* of command-line interface handling from the business logic 
of the application. This separation allows you to focus on the core functionality of your commands without worrying about 
how to parse arguments or handle user inputs. This additional behavior is *dynamic* in that the original function does not need to be modified.
The *advice* in this situation is the handling of command-line arguments in a reusable library.

## Summary
Decorators are a very powerful and useful tool in Python. They allow for cleaner and more readable code, especially when adding common functionality to multiple functions or methods. Understanding and using decorators can greatly enhance your Python programming skills.

Remember, while decorators are powerful, they should be used judiciously, as they can sometimes make your code more complex and harder to understand.